In [84]:
import pandas as pd
import numpy as np
import os 
import geopandas as gpd
import plotly.express as px
from scipy.spatial import KDTree
import plotly.graph_objects as go
from plotly.subplots import make_subplots

mf = gpd.read_file('./Marine_forest/Marine_forest.shp')
count = len(mf[(mf['면적'] == mf['구역']) & (mf['면적'] == mf['규모'])])
mf.drop(columns=['구역','규모'],inplace=True)
col_names = {'시도명': 'province','시군구명':'city','시군구코드':'city_code','위도':'latitude','경도':'longitude','마을어장':'town','면적':'area'}
mf.rename(columns=col_names, inplace=True)
#기본 칼럼인 위도 경도는 오류가 있었음
mf['latitude'] = mf['geometry'].y
mf['longitude'] = mf['geometry'].x

상관관계 분석 및 관련 논문을 참조한 결과,

1) 물리적 원인
가장 유력한 원인은 수온의 상승과 이로 인한 바닷속의 용존산소량의 감소
이 밖에도 다시마와 같은 해조류를 섭취하는 조식동물의 지나친 증식과 오염된 담수의 유입

2) 화학적 원인
해수의 저염수화(바다에 담수가 많이 유입되어 해수의 염도가 낮아짐)와 
해양오염(불투명도 증가와 오염물질의 확산)

따라서 
저희가 가지고 있는 데이터셋에서는
1. 수온, 2. 용존산소, 3. 염분,  4. 부유물질 농도 순으로 보면 될 것 같습니다!

칼럼별 상관계수 측정

In [85]:
df = pd.read_csv('./data/merged_data.csv')

df.drop(columns=['station', 'date_time', 'longitude', 'latitude','bot.depth[m]','depth(text)','depth(m)','전체수심(m)','유분[mg/L]','용존무기질소[μg/L]','아질산성질소[μg/L]', '인산염인[μg/L]',
       '질산성질소[μg/L]','암모니아성 질소[μg/L]'],inplace=True)
# 상관계수 계산
print(df.columns)
correlation_matrix = df.corr()
title = "Pearson Correlation Matrix"
fig = px.imshow(correlation_matrix, aspect="auto",title=title)
fig.update_layout(width=600, height=600, margin=dict(t=50, b=50, l=50, r=50))
fig.show()


Index(['총질소[μg/L]', '염분[psu]', '수온[℃]', '클로로필-a[μg/L]', '부유물질 농도[mg/L]',
       '용존산소[mg/L]', '수소이온농도[무단위]', '규산염[μg/L]', '투명도[m]', '화학적산소요구량[mg/L]',
       '총인[μg/L]', '부유물질 농도[μg/L]'],
      dtype='object')


In [86]:
spearman_corr = df.corr(method='kendall')
title = "Kendall Correlation Matrix"
fig = px.imshow(correlation_matrix, aspect="auto",title=title)
fig.update_layout(width=600, height=600, margin=dict(t=50, b=50, l=50, r=50))
fig.show()


In [87]:
spearman_corr = df.corr(method='spearman')
title = "Spearman Correlation Matrix"
fig = px.imshow(correlation_matrix, aspect="auto",title=title)
fig.update_layout(width=600, height=600, margin=dict(t=50, b=50, l=50, r=50))
fig.show()


# 바다숲 지형정보

바다숲 전체

In [88]:
title = '2013~2022년 바다숲 조성사업 현황'
buff = mf.loc[mf['시설년도'] <= 2022]
buff = buff.to_crs(epsg=32652)
scaling_factor = 1
center = {'lat': 35.8, 'lon': buff['longitude'].median()}
fig = px.scatter_mapbox(buff, lat=buff['latitude'], lon=buff['longitude'], size=(buff['area']* 10000)*scaling_factor,
                        color=buff['area'], size_max=20, zoom=5, center=center, title =title)
fig.update_layout(mapbox_style="open-street-map", margin={"r":10,"t":70,"l":20,"b":20},
                  width=1000 , height=800,legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1.15))
fig.show()

특정 년도마다 해양지형정보 측정기와 바다숲 위치정보

In [147]:
def map_scatter(title, ocean_loc):
    title = f'{title}'
    ocean_df  = pd.read_csv(f'{ocean_loc}')

    buff = mf.loc[mf['시설년도'] <= int(ocean_loc[-8:-4])]
    buff = buff.to_crs(epsg=32652)
    scaling_factor = 1
    center = {'lat': 35.8, 'lon': buff['longitude'].median()}
    fig = px.scatter_mapbox(buff, lat=buff['latitude'], lon=buff['longitude'], size=(buff['area']* 10000)*scaling_factor,
                            color=buff['area'], size_max=30, zoom=5, center=center, title =title)
    fig.add_trace(
        go.Scattermapbox(
            lat=ocean_df['latitude'],
            lon=ocean_df['longitude'],
            mode='markers',
            marker=dict(size=5, color='red'),  # 예시로 빨간색 마커를 사용
            
            name='Surface Data',
            
        )
    )
    fig.update_layout(mapbox_style="open-street-map", margin={"r":10,"t":70,"l":20,"b":20},
                    width=800 , height=800,legend=dict(orientation="h",yanchor="bottom",y=1.02,xanchor="right",x=1.15))

    fig.show()
#['클로로필-a[μg/L]','수소이온농도[무단위]', '규산염[μg/L]', '투명도[m]', '화학적산소요구량[mg/L]','총인[μg/L]', '부유물질 농도[mg/L]']
#1. 수온, 2. 용존산소, 3. 염분,  4. 부유물질 농도
def sc_by_col(ocean_path, origin_path, radius,title):
    # 데이터 불러오기
    columns_to_plot = ['수온[℃]','용존산소[mg/L]','염분[psu]','총질소[μg/L]', '부유물질 농도[mg/L]']
    ocean_df = pd.read_csv(ocean_path)
    origin = pd.read_csv(origin_path)

    # date_time 컬럼을 연-월 형식으로 변경
    ocean_df['date_time'] = pd.to_datetime(ocean_df['date_time'], format='mixed')
    ocean_df['date_time'] = pd.to_datetime(ocean_df['date_time']).dt.strftime('%Y-%m')
    origin['date_time'] = pd.to_datetime(origin['date_time'], format='mixed')
    origin['date_time'] = pd.to_datetime(origin['date_time']).dt.strftime('%Y-%m')

    # 동해, 서해, 남해 좌표 범위 설정
    regions = {
        '동해': [(128.5, 130), (34.5, 38.5)],
        '서해': [(124.5, 127), (34, 38)],
        '남해': [(126, 130), (33, 35)]
    }
    subplot_titles = []
    for col in columns_to_plot:
        for region in regions.keys():
            subplot_titles.append(f"{col} ({region})")
        subplot_titles.append(f"{col} (차이)")  # for the bar chart

    total_cols = len(regions) + 1  # +1 for the bar chart
    fig = make_subplots(rows=len(columns_to_plot), cols=total_cols, shared_xaxes=True, subplot_titles=subplot_titles)
    

    # Line plots
    for i, col in enumerate(columns_to_plot):
        for j, (region, (lon_range, lat_range)) in enumerate(regions.items()):
            filtered_ocean = ocean_df[(ocean_df['longitude'] >= lon_range[0]) & (ocean_df['longitude'] <= lon_range[1]) &
                                    (ocean_df['latitude'] >= lat_range[0]) & (ocean_df['latitude'] <= lat_range[1])]
            filtered_origin = origin[(origin['longitude'] >= lon_range[0]) & (origin['longitude'] <= lon_range[1]) &
                                    (origin['latitude'] >= lat_range[0]) & (origin['latitude'] <= lat_range[1])]
            
            ocean_avg = filtered_ocean.groupby('date_time')[col].mean().reset_index()
            origin_avg = filtered_origin.groupby('date_time')[col].mean().reset_index()
            
            fig.add_trace(go.Scatter(x=origin_avg['date_time'], y=origin_avg[col], mode="lines", 
                                    name=f"{region} 전체"), row=i+1, col=j+1)
            fig.add_trace(go.Scatter(x=ocean_avg['date_time'], y=ocean_avg[col], mode="lines", 
                                    name=f"바다숲 반경{radius}km"), row=i+1, col=j+1)
            

    # Bar chart for differences
    diffs = {}
    for region, (lon_range, lat_range) in regions.items():
        filtered_ocean = ocean_df[(ocean_df['longitude'] >= lon_range[0]) & (ocean_df['longitude'] <= lon_range[1]) &
                                (ocean_df['latitude'] >= lat_range[0]) & (ocean_df['latitude'] <= lat_range[1])]
        filtered_origin = origin[(origin['longitude'] >= lon_range[0]) & (origin['longitude'] <= lon_range[1]) &
                                (origin['latitude'] >= lat_range[0]) & (origin['latitude'] <= lat_range[1])]
        
        ocean_avg = filtered_ocean[columns_to_plot].mean()
        origin_avg = filtered_origin[columns_to_plot].mean()
        
        diffs[region] = origin_avg - ocean_avg

    for i, col in enumerate(columns_to_plot):
        y_values = [diffs[region][col] for region in regions]
        fig.add_trace(go.Bar(x=list(regions.keys()), y=y_values, name=col), row=i+1, col=total_cols)

    fig.update_layout(title = {
        'text' :title,
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top',
        'font': {
        'size': 24,
        'color': 'black',
                
        }},width=1500, height=100*len(columns_to_plot), margin=dict(t=100, b=40, l=40, r=40))
    fig.show()


## 2010년~ 2020년 해양환경 변화 시각화

해향지형정보 한 포인트당 겹치는 바다숲의 개수와 미치는 영향에 대해 알아봄
바다숲은 통상적으로 5년이상 되야 효과가 나타난다고 본거같음

먼저 kdTree를 활용해 좌표 거리를 계산, 특정 radius에 들어온 station을 df로 만들고 각 포인트 마다 정보의 변화를 찾기

['수온[℃]','용존산소[mg/L]','염분[psu]','총질소[μg/L]', '부유물질 농도[mg/L]']가 사용됨 더 많은 정보를 가져올수도 있음

## 2018년

차이가 양의 값을 가지면 전체의 평균이 더 큽니다.

In [93]:
ocean_df = pd.read_csv(f'data/surface/0.05/2018.csv')
origin = pd.read_csv('./data/2018.csv')
print(ocean_df.columns)
print(len(origin['station'].unique().tolist()))
unique_values = ocean_df['station'].unique().tolist()
print("개수:",len(unique_values))
fig = make_subplots(rows=5, cols=2)


for i, d in enumerate(unique_values[:10]):
    row = i // 2 + 1  # 행 결정
    col = i % 2 + 1   # 열 결정
    x = ocean_df.loc[ocean_df['station'] == d].sort_values(by='date_time').reset_index()
    
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['용존산소[mg/L]'], name=f'용존산소 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['총질소[μg/L]'], name=f'총질소 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['총인[μg/L]'], name=f'총인 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['용존무기질소[μg/L]'], name=f'용존무기질소 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['화학적산소요구량[mg/L]'], name=f'화학적산소요구량 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['염분[psu]'], name=f'화학적산소요구량 {d}'), row=row, col=col)
    fig.add_trace(go.Scatter(x=x['date_time'], y=x['아질산성질소[μg/L]'], name=f'아질산성질소 {d}'), row=row, col=col)

fig.update_layout(width=1200, height=1200, margin=dict(t=50, b=50, l=50, r=50))

fig.show()

Index(['station', 'date_time', 'longitude', 'latitude', '총질소[μg/L]', '염분[psu]',
       '수온[℃]', '클로로필-a[μg/L]', '부유물질 농도[mg/L]', '용존산소[mg/L]', '수소이온농도[무단위]',
       '규산염[μg/L]', '아질산성질소[μg/L]', '인산염인[μg/L]', '질산성질소[μg/L]', '투명도[m]',
       '용존무기질소[μg/L]', '화학적산소요구량[mg/L]', '암모니아성 질소[μg/L]', '총인[μg/L]',
       'overlap_count', '유분[mg/L]', '부유물질 농도[μg/L]'],
      dtype='object')


425
개수: 116


In [92]:
map_scatter("2018년도 해양지형정보, 바다숲 위치(5.555km)",'data/surface/0.05/2018.csv')

In [148]:
sc_by_col('data/surface/0.05/2018.csv','./data/surface/merged/2018.csv',5,'2018년 바다숲 반경 5km 표층')

저층- 5km반경- 2018년도 까지

차이가 양의 값을 가지면 전체의 평균이 더 큽니다.

In [149]:
sc_by_col('data/low/0.05/2018.csv','./data/surface/merged/2018.csv',5, '2018년 바다숲 반경 5km 저층')

1km

In [95]:
map_scatter("2018년도 해양지형정보, 바다숲 위치(1km)",'data/surface/0.01/2018.csv')

In [152]:
sc_by_col('data/surface/0.01/2018.csv','./data/surface/merged/2018.csv',1,"2018년 바다숲 반경 1km 저층")

## 2019

In [154]:
map_scatter("2019년도 해양지형정보, 바다숲 위치(5.555km)",'data/surface/0.05/2019.csv')
sc_by_col('data/surface/0.05/2019.csv','./data/surface/merged/2019.csv',5,'2018년 바다숲 반경 5km 표층')
sc_by_col('data/surface/0.05/2019.csv','./data/surface/merged/2019.csv',5,'2018년 바다숲 반경 5km 저층')

## 2020

In [155]:
map_scatter("2020년도 해양지형정보, 바다숲 위치(5.555km)",'data/surface/0.05/2020.csv')
sc_by_col('data/surface/0.05/2020.csv','./data/surface/merged/2020.csv',5,'2020년 바다숲 반경 5km 표층')
sc_by_col('data/surface/0.05/2020.csv','./data/surface/merged/2020.csv',5,'2020년 바다숲 반경 5km 저층')